# 1. Install optimization model package

In [2]:
!pip install -q pyomo
# solvers needed to be installed separately

# glpk
!apt-get install -y -qq glpk-utils

!pip install geopy

!pip install gurobipy  # install gurobipy, if not already installed
import gurobipy as gp  # import the installed package


     |████████████████████████████████| 9.7 MB 5.3 MB/s 
     |████████████████████████████████| 49 kB 3.6 MB/s 
Selecting previously unselected package libsuitesparseconfig5:amd64.
(Reading database ... 123991 files and directories currently installed.)
Preparing to unpack .../libsuitesparseconfig5_1%3a5.1.2-2_amd64.deb ...
Unpacking libsuitesparseconfig5:amd64 (1:5.1.2-2) ...
Selecting previously unselected package libamd2:amd64.
Preparing to unpack .../libamd2_1%3a5.1.2-2_amd64.deb ...
Unpacking libamd2:amd64 (1:5.1.2-2) ...
Selecting previously unselected package libcolamd2:amd64.
Preparing to unpack .../libcolamd2_1%3a5.1.2-2_amd64.deb ...
Unpacking libcolamd2:amd64 (1:5.1.2-2) ...
Selecting previously unselected package libglpk40:amd64.
Preparing to unpack .../libglpk40_4.65-1_amd64.deb ...
Unpacking libglpk40:amd64 (4.65-1) ...
Selecting previously unselected package glpk-utils.
Preparing to unpack .../glpk-utils_4.65-1_amd64.deb ...
Unpacking glpk-utils (4.65-1) ...
Setting up 

In [3]:
# check for license expiration date
model_size_limited = gp.Model()

Restricted license - for non-production use only - expires 2024-10-28


In [4]:
import pandas as pd
import numpy as np
from geopy import distance

# 2. Load Data

In [5]:
from google.colab import drive
drive.mount('/content/drive/')
%cd /content/drive/My Drive/Capstone-KPMG/Preprocessing
!ls

# main = pd.read_csv('Data/main_dataset.csv')
main = pd.read_csv('Data/main_dataset_all_interstate.csv')

main.columns

Mounted at /content/drive/
/content/drive/My Drive/Capstone-KPMG/Preprocessing
all_route_10mile_adjacent.pkl	 I5_south_10mile_adjacent.pkl
Attractions.ipynb		 I90.ipynb
combine_data.ipynb		 map_request_api.py
Combine.ipynb			 num_EV_chargers_around_gas.ipynb
Data				 OBSOLETE_Geo.ipynb
EV_station_count_distance.ipynb  OBSOLETE_remoteDataList
file.pkl			 __pycache__
gas_station_w_traffic.csv	 traffic_population_crime_combination.ipynb
HighwayExitDistance.ipynb


Index(['gas_key', 'gas_name', 'gas_lat', 'gas_long', 'attr_cnt_1mile',
       'attr_cnt_5mile', 'attr_name', 'attr_lat', 'attr_long',
       'distance_to_nearest_attr', 'crime_coord', 'crime_county',
       'crime_population', 'violent_crime', 'murder_nonnegligent_manslaughter',
       'Rape1', 'Robbery', 'aggravated_assault', 'property_crime', 'Burglary',
       'larceny_theft', 'motor_vehicle_theft', 'Arson', 'total_crime',
       'exit_name', 'exit_lat', 'exit_long', 'distance_to_nearest_exit',
       'exit', 'num_EV_in_2_miles_of_gas', 'num_EV_in_5_miles_of_gas',
       'num_EV_in_10_miles_of_gas', 'num_EV_in_20_miles_of_gas',
       'num_EV_in_50_miles_of_gas', 'Closest_EV_Station_name',
       'Closest_EV_Station_lat', 'Closest_EV_Station_long',
       'distance_to_closest_ev_station', 'nri_geoid', 'nri_county',
       'nri_population', 'nri_build_value', 'nri_agri_value', 'nri_area',
       'nri_risk_score', 'nri_risk_rating', 'nri_intpt_lat', 'nri_intpt_long',
       'nri_zipco

# 3. Optimization
*Objective function:* Minimize number of chargers/stations

*Constraints:*
- Distance to highway exit < 5 miles
- **All traffic covered (# EV stations * ratio < traffic around).**

Electric vehicles were 1.3% of all passenger vehicles on Washington roads

In [6]:
main['exit']

0       NaN
1       NaN
2       NaN
3       NaN
4       NaN
       ... 
2206    NaN
2207    NaN
2208    NaN
2209    NaN
2210    NaN
Name: exit, Length: 2211, dtype: object

In [7]:
df = main[main['exit'].notna()]
df.shape

(534, 55)

In [8]:
# filter out fixed constraint data
df = main[main['exit'] == 'I5']
df_x = df[df['distance_to_nearest_exit'] < 5]
# df_x = df_x[df_x['nri_risk_rating']!= 'Very High']
df_x.shape

(259, 55)

In [9]:
max(df_x['distance_to_nearest_exit'])

4.4273

In [10]:
max(df_x['distance_to_nearest_exit'])

4.4273

In [11]:
def get_adjacenct_gas(candidates, radius=2.5):
  # candidates = df_x['gas_key']
  adj = dict()
  for i in range(len(candidates)-1):
      for j in range(i+1, len(candidates)):
        # print(i,j)
        coords_1 = (main.iloc[candidates.iloc[i]]['gas_lat'], main.iloc[candidates.iloc[i]]['gas_long'])
        coords_2 = (main.iloc[candidates.iloc[j]]['gas_lat'], main.iloc[candidates.iloc[j]]['gas_long'])
        dist = distance.distance(coords_1, coords_2).miles
        if dist < radius: 
          if candidates.iloc[i] in adj:
            adj[candidates.iloc[i]].append(candidates.iloc[j])
          else:
            adj[candidates.iloc[i]] = [candidates.iloc[j]]
          if candidates.iloc[j] in adj:
            adj[candidates.iloc[j]].append(candidates.iloc[i])
          else:
            adj[candidates.iloc[j]] = [candidates.iloc[i]]
  return adj

def filter_gas(candidates):
  # remove adjacent gas stations from list, keep only one
  adj = get_adjacenct_gas(candidates)
  result = dict()
  for i in adj.keys():
    tmp = True
    if i in result: tmp = False
    for j in adj[i]:
      # print(j, j in result)
      if j in result: tmp = False
    if tmp: result[i] = len(adj[i])
  return result

In [12]:
# adj_sorted = {k: v for k, v in sorted(adj.items(), key=lambda item: len(item[1]))}
# adj_sorted

filtered_gas = filter_gas(df_x['gas_key'])

filtered_df = pd.DataFrame(filtered_gas.values(),index=filtered_gas.keys()).reset_index()
filtered_df = filtered_df.rename(columns={'index': 'gas_key', 0: 'nearby_gas'})
df_x_filtered = filtered_df.merge(df_x, how = 'right', right_on = 'gas_key', left_on = 'gas_key').dropna(subset = ['nearby_gas'])

## Start Optimization

In [13]:
import gurobipy as gp
from gurobipy import GRB

In [14]:
651.1960009738859/0.02*0.016

520.9568007791087

In [15]:

def ev_station_loc_optimize_station(input, p, ratio = 521):
  m = gp.Model()

  # variables
  A = input['gas_key'].tolist()
  # number of EVs nearby 5 miles -> dict
  n = input[['gas_key', 'num_EV_in_5_miles_of_gas']].set_index('gas_key').T.to_dict("index")['num_EV_in_5_miles_of_gas']
  # traffic count -> dict
  T = input[['gas_key', 'traff_cnt_5m_max']].set_index('gas_key').T.to_dict("index")['traff_cnt_5m_max'] # tried with avg

  G = input[['gas_key', 'nearby_gas']].set_index('gas_key').T.to_dict("index")['nearby_gas'] # tried with avg

  # Add gas station locations
  y = m.addVars(A, vtype=GRB.INTEGER, name='gas') #GRB.INTEGER => optimize charger #BINARY

  # Set objective function
  m.setObjective(y.sum(), GRB.MINIMIZE)

  # temporary facilities capacity constraints
  demand_constraints = m.addConstrs((ratio*(n[i]+y[i]) >= T[i]*p for i in A))
  print()
  m.optimize()

  result = {}
  # print(f"\n_____________Plan for temporary facilities______________________")
  for i in A:
    if (y[i].x > 0):
      print(f"Build an EV station at location {i}, {y[i].x}")
      result[i] = y[i].x
  return result


# 4. Plot Results

In [19]:
import folium

def plot_result(result):
  ev_station = pd.read_csv('Data/wa_EV_stations.csv')
  ev_station = ev_station[['Latitude','Longitude']]
  ev_station['type'] = 'EV'
  ev_station['color'] = 'grey'
  ev_station['radius'] = 50
  ev_station['gas_key'] = ''
  ev_station['charger_cnt'] = ''
  plot_df = ev_station


  for i in result.keys():
    new_df = pd.DataFrame([[main.iloc[i]['gas_lat'], main.iloc[i]['gas_long'], 'Proposed', 'blue', 100, str(i),result[i]]], columns=plot_df.columns)
    plot_df = pd.concat([plot_df, new_df], ignore_index=True)


  center = 46.2735210909813, -122.89553326963093

  m = folium.Map(location=center, 
                zoom_start=9,
                width=850,height=850)

  # Same as before... go through each home in set, make circle, and add to map.
  # This time we add a color using price and the colormap object
  for i in range(plot_df.shape[0]):
      folium.Circle(
          location=[plot_df.iloc[i]['Latitude'], plot_df.iloc[i]['Longitude']],
          # popup=plot_df.iloc[i]['gas_key'],
          popup=plot_df.iloc[i]['charger_cnt'],
          radius=100,
          fill=True,
          color = plot_df.iloc[i]['color'],
          fill_opacity=0.2
      ).add_to(m)

  return m


### 2022 p=0.016

In [21]:
result_dict = ev_station_loc_optimize_station(df_x_filtered, p=0.016)
print(f"\n\n\nSuggested {len(result_dict)} locations")
m = plot_result(result_dict)
m


Gurobi Optimizer version 10.0.0 build v10.0.0rc2 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Optimize a model with 35 rows, 35 columns and 35 nonzeros
Model fingerprint: 0xc70b6013
Variable types: 0 continuous, 35 integer (0 binary)
Coefficient statistics:
  Matrix range     [5e+02, 5e+02]
  Objective range  [1e+00, 1e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+02, 2e+04]
Found heuristic solution: objective 21.0000000
Presolve removed 35 rows and 35 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.06 seconds (0.00 work units)
Thread count was 1 (of 2 available processors)

Solution count 1: 21 

Optimal solution found (tolerance 1.00e-04)
Best objective 2.100000000000e+01, best bound 2.100000000000e+01, gap 0.0000%
Build an EV station at location 32, 2.0
Build an EV station at location 

### 2026 p = 0.03

In [18]:
result_dict = ev_station_loc_optimize_station(df_x_filtered, p=0.03)
print(f"\n\n\nSuggested {len(result_dict)} locations")
m = plot_result(result_dict)
m


Gurobi Optimizer version 10.0.0 build v10.0.0rc2 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Optimize a model with 35 rows, 35 columns and 35 nonzeros
Model fingerprint: 0x8cb70d2d
Variable types: 0 continuous, 35 integer (0 binary)
Coefficient statistics:
  Matrix range     [5e+02, 5e+02]
  Objective range  [1e+00, 1e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [2e+02, 2e+04]
Found heuristic solution: objective 46.0000000
Presolve removed 35 rows and 35 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.06 seconds (0.00 work units)
Thread count was 1 (of 2 available processors)

Solution count 1: 46 

Optimal solution found (tolerance 1.00e-04)
Best objective 4.600000000000e+01, best bound 4.600000000000e+01, gap 0.0000%
Build an EV station at location 16, 1.0
Build an EV station at location 

### 2030 p=0.05

In [ ]:
result_dict = ev_station_loc_optimize(df_x_filtered, p=0.05)
print(f"\n\n\nSuggested {len(result_dict)} locations")
m = plot_result(result_dict)
m


Gurobi Optimizer version 10.0.0 build v10.0.0rc2 (linux64)

CPU model: Intel(R) Xeon(R) CPU @ 2.20GHz, instruction set [SSE2|AVX|AVX2]
Thread count: 1 physical cores, 2 logical processors, using up to 2 threads

Optimize a model with 35 rows, 35 columns and 35 nonzeros
Model fingerprint: 0xd86336ab
Variable types: 0 continuous, 35 integer (0 binary)
Coefficient statistics:
  Matrix range     [5e+02, 5e+02]
  Objective range  [1e+00, 1e+00]
  Bounds range     [0e+00, 0e+00]
  RHS range        [6e+02, 2e+04]
Found heuristic solution: objective 92.0000000
Presolve removed 35 rows and 35 columns
Presolve time: 0.00s
Presolve: All rows and columns removed

Explored 0 nodes (0 simplex iterations) in 0.02 seconds (0.00 work units)
Thread count was 1 (of 2 available processors)

Solution count 1: 92 

Optimal solution found (tolerance 1.00e-04)
Best objective 9.200000000000e+01, best bound 9.200000000000e+01, gap 0.0000%
Build an EV station at location 16, 4.0
Build an EV station at location 

In [ ]:
print(pd.__version__)
print(np.__version__)
print(folium.__version__)
print(gp.gurobi.version())
import geopy as geo
print(geo.__version__)


1.3.5
1.21.6
0.12.1.post1
(10, 0, 0)
1.17.0
